# Thesis Pipline

## Installations

In [ ]:
!pip install --upgrade datasets sentence-transformers



   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.5/491.5 kB 25.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 kB 18.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 47.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 92.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 46.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 40.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 19.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 3.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 110.7 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitli

In [ ]:
from datasets import load_dataset
full_dataset = load_dataset("gsm8k", "main", split="test")
dataset = full_dataset.shuffle(seed=42).select(range(300))


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/7.94k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/2.31M [00:00<?, ?B/s]

test-00000-of-00001.parquet:   0%|          | 0.00/419k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/7473 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1319 [00:00<?, ? examples/s]

## Stage1 Shap_gpt2

In [ ]:
# stage1_shap_gpt2

import shap
import torch
import numpy as np
import pandas as pd
from datasets import load_dataset
from transformers import GPT2Tokenizer, GPT2LMHeadModel

# Load and sample 100 from the test set
full_dataset = load_dataset("gsm8k", "main", split="test")
dataset = full_dataset.shuffle(seed=42).select(range(300)) # 200/300

questions = [{
    "core_question": item["question"],
    "gold_answer": item["answer"].split("####")[-1].strip(),
    "gold_reasoning": item["answer"].strip()  # full solution
} for item in dataset]

# Load GPT-2
tokenizer = GPT2Tokenizer.from_pretrained("gpt2")
model = GPT2LMHeadModel.from_pretrained("gpt2")
model.eval()

def logprob_fn(texts, target_token_id):
    scores = []
    for text in texts:
        input_ids = tokenizer.encode(text, return_tensors="pt")
        with torch.no_grad():
            logits = model(input_ids).logits
        probs = torch.softmax(logits[0, -1], dim=0)
        logprob = torch.log(probs[target_token_id])
        scores.append(logprob.item())
    return np.array(scores)

# Collect SHAP results
shap_results = []

for q in questions:
    prompt = q["core_question"]
    target_token_id = tokenizer.encode(q["gold_answer"])[0]

    masker = shap.maskers.Text(tokenizer)
    explainer = shap.Explainer(lambda x: logprob_fn(x, target_token_id), masker)
    shap_values = explainer([prompt])

    tokens = shap_values[0].data
    values = shap_values[0].values
    pairs = sorted(zip(tokens, values), key=lambda x: x[1], reverse=True)

    top_tokens = [tok.replace("Ġ", "") for tok, val in pairs[:5]]
    shap_results.append({
        "question_text": prompt,
        "gold_answer": q["gold_answer"],
        "gold_reasoning": q["gold_reasoning"],
        "top_shap_tokens": top_tokens
    })

df = pd.DataFrame(shap_results)
df.to_csv("shap_top_tokens.csv", index=False)
print("✅ SHAP results saved including full gold reasoning.")


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

...

  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:35, 35.44s/it]               


  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 2it [00:34, 34.40s/it]               

✅ SHAP results saved including full gold reasoning.


## Stage2 Qwen Reasoning

In [ ]:
import random
import re
import torch
import math
import pandas as pd
from transformers import AutoTokenizer, AutoModelForCausalLM, GPT2Tokenizer, GPT2LMHeadModel
from sentence_transformers import SentenceTransformer, util


In [ ]:
# Load SHAP DataFrame
df_shap = pd.read_csv("shap_top_tokens (2).csv")

# Distractor sentences
distractor_pool = [
    "There are 7 chairs in the room.",
    "His friend Lisa has 20 books.",
    "The class starts at 8 o'clock.",
    "She counted 23 birds in the park.",
    "A train arrives at 6 PM."
]


In [ ]:
# Load target model
model_name = "Qwen/Qwen2.5-7B-Instruct"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)
device = "cuda" if torch.cuda.is_available() else "cpu"
model.to(device)
model.eval()

# Load sentence similarity model
embedding_model = SentenceTransformer("all-MiniLM-L6-v2")

# Load GPT-2 for perplexity scoring
gpt2_model = GPT2LMHeadModel.from_pretrained("gpt2").eval()
gpt2_tokenizer = GPT2Tokenizer.from_pretrained("gpt2")


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/7.30k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/2.78M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/1.67M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/7.03M [00:00<?, ?B/s]

...

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

In [4]:
def generate_answer(prompt, temperature=1.0, max_new_tokens=256):
    input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)
    with torch.no_grad():
        output = model.generate(
            input_ids,
            max_new_tokens=max_new_tokens,
            temperature=temperature,
            do_sample=(temperature > 0.0),  # use sampling only when temperature > 0
            pad_token_id=tokenizer.eos_token_id
        )
    return tokenizer.decode(output[0][input_ids.shape[1]:], skip_special_tokens=True).strip()


def compute_cosine_similarity(text1, text2):
    emb1 = embedding_model.encode(text1, convert_to_tensor=True)
    emb2 = embedding_model.encode(text2, convert_to_tensor=True)
    return float(util.cos_sim(emb1, emb2))

def compute_perplexity(text):
    input_ids = gpt2_tokenizer.encode(text, return_tensors='pt')
    with torch.no_grad():
        output = gpt2_model(input_ids, labels=input_ids)
    loss = output.loss.item()
    return math.exp(loss)


In [ ]:
import os

checkpoint_path = "partial_results.csv"
all_results = []

# Resume from checkpoint if it exists
if os.path.exists(checkpoint_path):
    existing_df = pd.read_csv(checkpoint_path)
    completed_keys = set(zip(existing_df["question"], existing_df["variant"], existing_df["temperature"]))
    all_results.extend(existing_df.to_dict("records"))
    print(f"🔁 Resuming from {len(all_results)} previous results.")
else:
    completed_keys = set()



# 2. Add temperature loop
temperatures = [0.0, 0.5, 1.0]

batch_size = 50  # save every 50 examples
counter = 0

for _, row in df_shap.iterrows():
    base = row["question_text"]
    answer = row["gold_answer"]
    gold_reasoning = row["gold_reasoning"]
    top_tokens = eval(row["top_shap_tokens"])
    focus = ", ".join(top_tokens)
    distractors = random.sample(distractor_pool, 2)
    distractor_text = " ".join(distractors)

    variants = {
        "original": {
            "text": base,
            "distractors_used": [],
            "has_distractor": False
        },
        "original+focused": {
            "text": f"{base}.\n\n Focus on these important parts: {focus}",
            "distractors_used": [],
            "has_distractor": False
        },
        "original+distractor": {
            "text": base + " " + distractor_text,
            "distractors_used": distractors,
            "has_distractor": True
        },
        "original+distractor+focused": {
            "text": f"\n\n{base}. {distractor_text}. Focus on these important parts: {focus}",
            "distractors_used": distractors,
            "has_distractor": True
        }
    }

    for vtype, vdata in variants.items():
        for temp in temperatures:
            key = (base, vtype, temp)
            if key in completed_keys:
                continue

            prompt = vdata["text"]
            model_answer = generate_answer(prompt, temperature=temp)
            answer_position = model_answer.find(str(answer))
            reasoning_similarity = compute_cosine_similarity(gold_reasoning, model_answer)
            fluency_score = compute_perplexity(prompt)

            result = {
                "question": base,
                "gold_reasoning": gold_reasoning,
                "gold_answer": answer,
                "variant": vtype,
                "temperature": temp,
                "prompt": prompt,
                "top_tokens": top_tokens,
                "has_distractor": vdata["has_distractor"],
                "distractors_used": vdata["distractors_used"],
                "model_answer": model_answer,
                "prompt_length": len(tokenizer.tokenize(prompt)),
                "answer_position": answer_position,
                "reasoning_cosine_similarity": reasoning_similarity,
                "fluency_score": fluency_score
            }

            all_results.append(result)
            counter += 1

            if counter % batch_size == 0:
                pd.DataFrame(all_results).to_csv(checkpoint_path, index=False)
                print(f"💾 Saved checkpoint after {counter} results")



The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p'

💾 Saved checkpoint after 50 results


The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p'

💾 Saved checkpoint after 100 results


The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p'

...

💾 Saved checkpoint after 3500 results


The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p'

💾 Saved checkpoint after 3550 results


The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p'

💾 Saved checkpoint after 3600 results


In [ ]:
df_final = pd.DataFrame(all_results)
df_final.to_csv("qwen_prompt_variant_results.csv", index=False)
print("✅ Qwen evaluation results saved to qwen_prompt_variant_results.csv")

✅ Qwen evaluation results saved to qwen_prompt_variant_results.csv


## Stage 3 judge_answers

In [ ]:


import pandas as pd
import re

# Simple rule-based judge: check if gold answer is mentioned in reasoning
def judge_by_containment(gold_answer, model_output):
    if pd.isna(gold_answer) or pd.isna(model_output):
        return False
    pattern = rf"(?<!\d){re.escape(str(gold_answer))}(?!\d)"
    return bool(re.search(pattern, str(model_output)))


# Load and evaluate answers
df = pd.read_csv("qwen_prompt_variant_results.csv")
df["correct"] = df.apply(lambda row: judge_by_containment(row["gold_answer"], row["model_answer"]), axis=1)
# Final save
final_path = "judged_results.csv"
df.to_csv(final_path, index=False)
print("✅ Final judged results saved to judged_results.csv")





✅ Final judged results saved to judged_results.csv


In [ ]:
# Trigger download to your local machine
from google.colab import files
files.download(final_path)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Import Final Dataframe After Generation

In [12]:
import pandas as pd
df = pd.read_csv("judged_results.csv")
display(df)

question  \
0   Darrell and Allen's ages are in the ratio of 7...   
1   Darrell and Allen's ages are in the ratio of 7...   
2   Darrell and Allen's ages are in the ratio of 7...   
3   Darrell and Allen's ages are in the ratio of 7...   
4   Darrell and Allen's ages are in the ratio of 7...   
..                                                ...   
95  Jonathan has 2/3 as many measuring spoons as m...   
96  Martha's cat is 5 times faster than her turtle...   
97  Martha's cat is 5 times faster than her turtle...   
98  Martha's cat is 5 times faster than her turtle...   
99  Martha's cat is 5 times faster than her turtle...   

                                       gold_reasoning gold_answer  \
0   The total ratio representing their ages is 7+1...         109   
1   The total ratio representing their ages is 7+1...         109   
2   The total ratio representing their ages is 7+1...         109   
3   The total ratio representing their ages is 7+1...         109   
4   The total ratio representing their ages is 7+1...         109   
..                                                ...         ...   
95  A dozen measuring cups are 12, and if Jonathan...          34   
96  First find the speed of the turtle by dividing...         120   
97  First find the speed of the turtle by dividing...         120   
98  First find the speed of the turtle by dividing...         120   
99  First find the speed of the turtle by dividing...         120   

                        variant  temperature  \
0                      original          0.0   
1                      original          0.5   
2                      original          1.0   
3              original+focused          0.0   
4              original+focused          0.5   
..                          ...          ...   
95  original+distractor+focused          1.0   
96                     original          0.0   
97                     original          0.5   
98                     original          1.0   
99             original+focused          0.0   

                                               prompt  \
0   Darrell and Allen's ages are in the ratio of 7...   
1   Darrell and Allen's ages are in the ratio of 7...   
2   Darrell and Allen's ages are in the ratio of 7...   
3   Darrell and Allen's ages are in the ratio of 7...   
4   Darrell and Allen's ages are in the ratio of 7...   
..                                                ...   
95  \n\nJonathan has 2/3 as many measuring spoons ...   
96  Martha's cat is 5 times faster than her turtle...   
97  Martha's cat is 5 times faster than her turtle...   
98  Martha's cat is 5 times faster than her turtle...   
99  Martha's cat is 5 times faster than her turtle...   

                                top_tokens  has_distractor  \
0   [' 162', ' .', ' total', ' 11', ' 10']           False   
1   [' 162', ' .', ' total', ' 11', ' 10']           False   
2   [' 162', ' .', ' total', ' 11', ' 10']           False   
3   [' 162', ' .', ' total', ' 11', ' 10']           False   
4   [' 162', ' .', ' total', ' 11', ' 10']           False   
..                                     ...             ...   
95   [' .', ' 3', ' 6', ' Jonathan', ' 2']            True   
96     [' 15', ' 40', ' ?', ' /', ' feet']           False   
97     [' 15', ' 40', ' ?', ' /', ' feet']           False   
98     [' 15', ' 40', ' ?', ' /', ' feet']           False   
99     [' 15', ' 40', ' ?', ' /', ' feet']           False   

                                     distractors_used  \
0                                                  []   
1                                                  []   
2                                                  []   
3                                                  []   
4                                                  []   
..                                                ...   
95  ['A train arrives at 6 PM.', 'His friend Lisa ...   
96                                                 []   
97         

## Relevant Accuracy Measures

In [18]:
import pandas as pd

# Load your final results DataFrame
df = pd.read_csv("judged_results.csv")

# Ensure correctness is boolean
df["correct"] = df["correct"].astype(bool)

# Summary 1: Accuracy by Prompt Variant
accuracy_by_variant = df.groupby("variant")["correct"].mean().reset_index().rename(columns={"correct": "accuracy"})
print("\n Accuracy by Prompt Variant:")
print(accuracy_by_variant)

# Summary 2: Accuracy by Temperature
accuracy_by_temp = df.groupby("temperature")["correct"].mean().reset_index().rename(columns={"correct": "accuracy"})
print("\n Accuracy by Temperature:")
print(accuracy_by_temp)

# Summary 3: Accuracy by Variant and Temperature
accuracy_variant_temp = df.groupby(["variant", "temperature"])["correct"].mean().reset_index().rename(columns={"correct": "accuracy"})
print("\n Accuracy by Variant and Temperature:")
print(accuracy_variant_temp)

# Summary 4: Average Reasoning Similarity by Variant
similarity_by_variant = df.groupby("variant")["reasoning_cosine_similarity"].mean().reset_index().rename(columns={"reasoning_cosine_similarity": "avg_cosine_similarity"})
print("\n Reasoning Similarity by Variant:")
print(similarity_by_variant)

# Summary 5: Fluency Score by Variant
fluency_by_variant = df.groupby("variant")["fluency_score"].mean().reset_index().rename(columns={"fluency_score": "avg_fluency"})
print("\n Fluency Score by Variant:")
print(fluency_by_variant)

# Summary 6: Accuracy with vs without Distractor
accuracy_by_distractor = df.groupby("has_distractor")["correct"].mean().reset_index().rename(columns={"correct": "accuracy"})
print("\n Accuracy by Distractor Presence:")
print(accuracy_by_distractor)



# Ensure correctness column is boolean
df["correct"] = df["correct"].astype(bool)

# Print average accuracy and fluency per variant
agg = df.groupby("variant").agg(
    accuracy=("correct", "mean"),
    fluency=("fluency_score", "mean")
).reset_index()

print(" Accuracy and Fluency by Prompt Variant:\n")
for _, row in agg.iterrows():
    print(f"{row['variant']:30} | Accuracy: {row['accuracy']:.3f} | Fluency: {row['fluency']:.2f}")




📊 Accuracy by Prompt Variant:
                       variant  accuracy
0                     original  0.575556
1          original+distractor  0.611111
2  original+distractor+focused  0.547778
3             original+focused  0.518889

🌡️ Accuracy by Temperature:
   temperature  accuracy
0          0.0  0.544167
1          0.5  0.552500
2          1.0  0.593333

🧪 Accuracy by Variant and Temperature:
                        variant  temperature  accuracy
0                      original          0.0  0.566667
1                      original          0.5  0.546667
2                      original          1.0  0.613333
3           original+distractor          0.0  0.586667
4           original+distractor          0.5  0.603333
5           original+distractor          1.0  0.643333
6   original+distractor+focused          0.0  0.550000
7   original+distractor+focused          0.5  0.536667
8   original+distractor+focused          1.0  0.556667
9              original+focused          0.0 

### Human Evaluation

In [12]:
import pandas as pd
df = pd.read_csv("/content/judged_results (2) 15.42.59.csv")
low_sim_df = df[["gold_reasoning", "model_answer", "reasoning_cosine_similarity"]]
display(low_sim_df)

gold_reasoning  \
0     The total ratio representing their ages is 7+1...   
1     The total ratio representing their ages is 7+1...   
2     The total ratio representing their ages is 7+1...   
3     The total ratio representing their ages is 7+1...   
4     The total ratio representing their ages is 7+1...   
...                                                 ...   
3595  The total charge for the doughnuts was 3 x $68...   
3596  The total charge for the doughnuts was 3 x $68...   
3597  The total charge for the doughnuts was 3 x $68...   
3598  The total charge for the doughnuts was 3 x $68...   
3599  The total charge for the doughnuts was 3 x $68...   

                                           model_answer  \
0     To determine Allen's age 10 years from now, we...   
1     Let's denote Darrell's current age as \( D \) ...   
2     Let's denote Darrell's current age as \( D \) ...   
3     To solve this problem, we need to determine th...   
4     To solve this problem, we need to determine th...   
...                                                 ...   
3595  Then, 47 more birds joined them. So, in total ...   
3596  Then, 15 more birds joined them. How many bird...   
3597  ,  55,  dozen,  80,  3,  6. What's the answer?...   
3598  ,  55,  dozen,  80,  3,  6\n\nTo calculate the...   
3599  ,  55,  dozens. What is the total amount spent...   

      reasoning_cosine_similarity  
0                        0.811538  
1                        0.718129  
2                        0.722062  
3                        0.760607  
4                        0.772550  
...                           ...  
3595                     0.720666  
3596                     0.702513  
3597                     0.741818  
3598                     0.722267  
3599                     0.723295  

[3600 rows x 3 columns]

from matplotlib import pyplot as plt
_df_0['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_1['reasoning_cosine_similarity'].plot(kind='hist', bins=20, title='reasoning_cosine_similarity')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_2.plot(kind='scatter', x='index', y='reasoning_cosine_similarity', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  xs = series['index']
  ys = series['reasoning_cosine_similarity']
  
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_3.sort_values('index', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('index')
_ = plt.ylabel('reasoning_cosine_similarity')

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['index']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'index'}, axis=1)
              .sort_values('index', ascending=True))
  xs = counted['index']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_4.sort_values('index', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('index')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
_df_5['index'].plot(kind='line', figsize=(8, 4), title='index')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_6['reasoning_cosine_similarity'].plot(kind='line', figsize=(8, 4), title='reasoning_cosine_similarity')
plt.gca().spines[['top', 'right']].set_visible(False)

## Relevant Visualizations

In [24]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import ast
from collections import Counter

# Load the dataset
df = pd.read_csv("judged_results.csv")

# Convert stringified lists to actual lists
df["top_tokens"] = df["top_tokens"].apply(ast.literal_eval)
df["correct"] = df["correct"].astype(bool)

# 1. Accuracy by Prompt Variant
def plot_accuracy_by_variant(df):
    acc_by_variant = df.groupby("variant")["correct"].mean().reset_index()
    plt.figure(figsize=(8, 5))
    sns.barplot(
        data=acc_by_variant,
        x="variant",
        y="correct",
        color="#FFCD00"
    )
    plt.title("Accuracy by Prompt Variant")
    plt.ylabel("Accuracy")
    plt.ylim(0, 1)
    plt.grid(True)
    plt.tight_layout()
    plt.savefig("accuracy_by_variant.png")
    plt.close()

# 2. Prompt Length vs Correctness
def plot_prompt_length_vs_correct(df):
    plt.figure(figsize=(8, 5))
    sns.boxplot(data=df, x="correct", y="prompt_length")
    plt.title("Prompt Length vs Correctness")
    plt.xlabel("Correct")
    plt.ylabel("Prompt Length")
    plt.grid(True)
    plt.tight_layout()
    plt.savefig("prompt_length_vs_correct.png")
    plt.close()

def plot_reasoning_cosine_similarity(df):
    plt.figure(figsize=(8, 5))
    sns.violinplot(
        data=df,
        x="variant",
        y="reasoning_cosine_similarity",
        palette=["#FFCD00"]
    )
    plt.title("Cosine Similarity Between Model and Gold Reasoning")
    plt.ylabel("Cosine Similarity")
    plt.ylim(0, 1)
    plt.grid(True)
    plt.tight_layout()
    plt.savefig("reasoning_similarity_by_variant.png")
    plt.close()

# 4. Fluency Score vs Correctness
def plot_fluency_vs_correct(df):
    plt.figure(figsize=(8, 5))
    sns.boxplot(data=df, x="correct", y="fluency_score")
    plt.title("Fluency Score vs Correctness")
    plt.xlabel("Correct")
    plt.ylabel("Fluency Score")
    plt.grid(True)
    plt.tight_layout()
    plt.savefig("fluency_vs_correct.png")
    plt.close()

# 5. Accuracy by Temperature
def plot_accuracy_by_temperature(df):
    acc_by_temp = df.groupby("temperature")["correct"].mean().reset_index()
    plt.figure(figsize=(8, 5))

    sns.lineplot(
        data=acc_by_temp,
        x="temperature",
        y="correct",
        color="#FFCD00",
        linewidth=5,
        marker=None
    )

    plt.scatter(
        acc_by_temp["temperature"],
        acc_by_temp["correct"],
        color="#333333",
        s=100,
        zorder=5
    )

    plt.title("Accuracy by Temperature")
    plt.ylabel("Accuracy")
    plt.ylim(0, 1)
    plt.grid(True)
    plt.tight_layout()
    plt.savefig("accuracy_by_temperature.png")
    plt.close()

# 6. Accuracy by Prompt Variant Across Temperatures
def plot_accuracy_by_variant_and_temperature(df):
    acc = df.groupby(["variant", "temperature"])["correct"].mean().reset_index()
    plt.figure(figsize=(10, 6))
    sns.lineplot(data=acc, x="temperature", y="correct", hue="variant", marker="o")
    plt.title("Accuracy by Prompt Variant Across Temperatures")
    plt.ylabel("Accuracy")
    plt.ylim(0, 1)
    plt.grid(True)
    plt.tight_layout()
    plt.savefig("accuracy_by_variant_and_temperature.png")
    plt.close()

# 7. Cosine Similarity by Temperature
def plot_similarity_by_temperature(df):
    plt.figure(figsize=(8, 5))
    sns.boxplot(data=df, x="temperature", y="reasoning_cosine_similarity")
    plt.title("Reasoning Cosine Similarity by Temperature")
    plt.ylabel("Cosine Similarity")
    plt.ylim(0, 1)
    plt.grid(True)
    plt.tight_layout()
    plt.savefig("reasoning_similarity_by_temperature.png")
    plt.close()

# 8. Fluency Distribution by Temperature
def plot_fluency_distribution(df):
    plt.figure(figsize=(8, 5))
    sns.violinplot(data=df, x="temperature", y="fluency_score")
    plt.title("Fluency Score Distribution by Temperature")
    plt.grid(True)
    plt.tight_layout()
    plt.savefig("fluency_distribution_by_temperature.png")
    plt.close()

# 9. Heatmap: Correctness by Variant and Temperature
def plot_correctness_heatmap(df):
    heatmap_data = df.groupby(["variant", "temperature"])["correct"].mean().unstack()
    plt.figure(figsize=(10, 6))
    sns.heatmap(heatmap_data, annot=True, fmt=".2f", cmap="YlGnBu")
    plt.title("Correctness Rate by Variant and Temperature")
    plt.xlabel("Temperature")
    plt.ylabel("Prompt Variant")
    plt.tight_layout()
    plt.savefig("correctness_heatmap.png")
    plt.close()

# 10. Accuracy by Distractor Presence
def plot_accuracy_by_distractor(df):
    acc = df.groupby("has_distractor")["correct"].mean().reset_index()
    plt.figure(figsize=(6, 4))
    sns.barplot(data=acc, x="has_distractor", y="correct")
    plt.title("Accuracy by Distractor Presence")
    plt.ylabel("Accuracy")
    plt.ylim(0, 1)
    plt.tight_layout()
    plt.savefig("accuracy_by_distractor_presence.png")
    plt.close()

def plot_dual_axis_accuracy_fluency(df):
    agg = df.groupby("variant").agg(
        accuracy=("correct", "mean"),
        fluency=("fluency_score", "mean")
    ).reset_index()

    fig, ax1 = plt.subplots(figsize=(10, 6))
    ax2 = ax1.twinx()

    ax1.plot(agg["variant"], agg["accuracy"], color="blue", marker="o", label="Accuracy")
    ax2.plot(agg["variant"], agg["fluency"], color="green", marker="s", label="Fluency")

    ax1.set_ylabel("Accuracy", color="blue")
    ax2.set_ylabel("Fluency", color="green")
    ax1.set_title("Accuracy and Fluency by Prompt Variant")
    ax1.set_xticklabels(agg["variant"], rotation=45)
    ax1.set_ylim(0, 1)
    ax2.set_ylim(0, agg["fluency"].max() * 1.1)

    fig.tight_layout()
    plt.savefig("accuracy_fluency_dual_axis_by_variant.png")
    plt.close()


# Call and save all plots
plot_accuracy_by_variant(df)
plot_prompt_length_vs_correct(df)
plot_reasoning_cosine_similarity(df)
plot_fluency_vs_correct(df)
plot_accuracy_by_temperature(df)
plot_accuracy_by_variant_and_temperature(df)
plot_similarity_by_temperature(df)
plot_fluency_distribution(df)
plot_correctness_heatmap(df)
plot_accuracy_by_distractor(df)
plot_dual_axis_accuracy_fluency(df)



/tmp/ipython-input-24-3905846665.py:46: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `x` variable to `hue` and set `legend=False` for the same effect.

  sns.violinplot(
/tmp/ipython-input-24-3905846665.py:46: UserWarning: 
The palette list has fewer values (1) than needed (4) and will cycle, which may produce an uninterpretable plot.
  sns.violinplot(


✅ All plots saved to the current directory.
